
# Project : Geospatial Data Analysis and Interactive Visualization


## Importing the necessary libraries

In [6]:
import pandas as pd 
import numpy as np
import warnings 
import matplotlib.pyplot as plt
import seaborn as sns
import scipy.stats
warnings.filterwarnings('ignore')
pd.set_option("display.max_columns", None)

# Step - 1: Data Acquisition and Inspection
## Loading the dataset

In [ ]:

dataset = pd.read_csv("2024-11-22-iolp-leases.csv", encoding='latin1')




## Initial Inspection

In [8]:
# Inspect the structure and data types of the dataset
dataset.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7588 entries, 0 to 7587
Data columns (total 19 columns):
 #   Column                                 Non-Null Count  Dtype  
---  ------                                 --------------  -----  
 0   Location Code                          7588 non-null   object 
 1   Real Property Asset Name               7588 non-null   object 
 2   Installation Name                      48 non-null     object 
 3   Federal Leased Code                    7588 non-null   object 
 4   GSA Region                             7588 non-null   int64  
 5   Street Address                         7588 non-null   object 
 6   City                                   7588 non-null   object 
 7   State                                  7588 non-null   object 
 8   Zip Code                               7588 non-null   int64  
 9   Latitude                               7588 non-null   float64
 10  Longitude                              7588 non-null   float64
 11  Buil

In [9]:
# To get the number of rows , column in the daatset
print("Number of Rows in Inventory Dataset : " + str(dataset.shape[0]))
print("Number of Columns in Inventory Dataset : " + str(dataset.shape[1]))

Number of Rows in Inventory Dataset : 7588
Number of Columns in Inventory Dataset : 19


In [10]:
# Display the first few rows of the dataset
dataset.head()

Location Code Real Property Asset Name Installation Name  \
0        AK0009     POST OFFICE AND CU H               NaN   
1        AK3139           TROUTTE CENTER               NaN   
2        AK3166           PETERSON TOWER               NaN   
3        AK3177     TUDOR BUSINESS CNTER               NaN   
4        AK3180         MICHAEL BUILDING               NaN   

  Federal Leased Code  GSA Region   Street Address       City State  Zip Code  \
0                   L          10           2ND ST   WRANGELL    AK     99929   
1                   L          10    329 HARBOR DR      SITKA    AK     99835   
2                   L          10         510 L ST  ANCHORAGE    AK     99501   
3                   L          10  1011 E TUDOR RD  ANCHORAGE    AK     99503   
4                   L          10   620 E 10TH AVE  ANCHORAGE    AK     99501   

    Latitude  Longitude  Building Rentable Square Feet  Available Square Feet  \
0  56.473949 -132.38812                           97.0                    0.0   
1  57.050285 -135.33364                          951.0                    0.0   
2  61.217147 -149.90432                         5283.0                    0.0   
3  61.182111 -149.86311                        89049.0                    0.0   
4  61.212371 -149.87231                        25515.0                    0.0   

   Congressional District Congressional District Representative Lease Number  \
0                     200                          MARY PELTOLA     LAK00348   
1                     200                          MARY PELTOLA     LAK07113   
2                     200                          MARY PELTOLA     LAK07230   
3                     200                          MARY PELTOLA     LAK07436   
4                     200                          MARY PELTOLA     LAK06502   

  Lease Effective Date Lease Expiration Date Real Property Asset type  
0           2022-10-01            2027-09-30                 BUILDING  
1           2009-04-17            2029-04-16                 BUILDING  
2           2011-05-12            2028-12-31                 BUILDING  
3           2015-11-22            2035-11-21                 BUILDING  
4           2003-05-01            2028-04-30                 BUILDING

Insights:

1. The dataset contains 7,588 rows and 19 columns.

2. Data types include: 

    int64 for numerical data (e.g., GSA Region, Zip code, Congressional District).

    float64 for numerical data with decimals (e.g., Latitude, Longitude).
    
    object for text data (e.g., Location Code, Real Property Asset Name, Street Address).

    object for datetime (e.g., Lease Effective Date, Lease Expiration Date)

In [11]:
# Features of housing dataset
features = dataset.columns
print(features)

Index(['Location Code', 'Real Property Asset Name', 'Installation Name',
       'Federal Leased Code', 'GSA Region', 'Street Address', 'City', 'State',
       'Zip Code', 'Latitude', 'Longitude', 'Building Rentable Square Feet',
       'Available Square Feet', 'Congressional District',
       'Congressional District Representative', 'Lease Number',
       'Lease Effective Date', 'Lease Expiration Date',
       'Real Property Asset type'],
      dtype='object')


In [12]:
# Investigate unique values for each feature
for column in dataset.columns:
    num_unique = dataset[column].nunique()
    unique_values = dataset[column].unique()
    print(f"Unique values in column '{column}': {num_unique}")
    print(unique_values)
    print()

Unique values in column 'Location Code': 6485
['AK0009' 'AK3139' 'AK3166' ... 'WY1357' 'WY1359' 'WY1362']

Unique values in column 'Real Property Asset Name': 6532
['POST OFFICE AND CU H' 'TROUTTE CENTER' 'PETERSON TOWER' ...
 'FOREST SERVICE S.O. OFFICE' 'DOUGLAS FOREST SERVICE BUILDING'
 'FIRST INTERSTATE BANK']

Unique values in column 'Installation Name': 14
[nan 'CORPS OF ENGINEERS' 'ANDRADE LPOE' 'APPRAISERS STORE'
 'METRO PLAZA COMPLEX' 'WESTWOOD' 'GSA/PMDS DEPOT' 'USBS HIDALGO'
 'USBS ROMA' 'STAR-CAMARGO BRIDGE' 'USBS STANTON ST EL PASO'
 'USBS PROGRESO' 'USBS PRESIDIO' 'ADMIN BLDG/ADM GA' 'REUSS PLAZA']

Unique values in column 'Federal Leased Code': 1
['L']

Unique values in column 'GSA Region': 11
[10  4  7  9  8  1 11  3  6  5  2]

Unique values in column 'Street Address': 6419
['2ND ST' '329 HARBOR DR' '510 L ST' ... '808 MEADOW LANE AVE'
 '2250 E RICHARDS ST' '104 S WOLCOTT ST']

Unique values in column 'City': 1829
['WRANGELL' 'SITKA' 'ANCHORAGE' ... 'LARAMIE' 'KEMMERER'

# Step - 2 : Data Cleaning and Preparation

In [13]:
# Making a copy of the dataset.
df_copy = dataset.copy() 

## Address missing data, duplicates, and inconsistencies.

In [14]:
# Remove duplicates
df_copy = df_copy.drop_duplicates()

In [15]:
# 1. Handle missing values
# Check the missing values
df_copy.isnull().sum()

Location Code                               0
Real Property Asset Name                    0
Installation Name                        7540
Federal Leased Code                         0
GSA Region                                  0
Street Address                              0
City                                        0
State                                       0
Zip Code                                    0
Latitude                                    0
Longitude                                   0
Building Rentable Square Feet               0
Available Square Feet                       0
Congressional District                      0
Congressional District Representative       0
Lease Number                                0
Lease Effective Date                        0
Lease Expiration Date                       0
Real Property Asset type                    0
dtype: int64

- The "Installation Name" column has 99.37% missing values, and since most records lack an installation name, we will drop this column.

In [16]:
df_copy = df_copy.drop(columns="Installation Name")

In [17]:
# Check after dropping missing values
df_copy.isnull().sum()

Location Code                            0
Real Property Asset Name                 0
Federal Leased Code                      0
GSA Region                               0
Street Address                           0
City                                     0
State                                    0
Zip Code                                 0
Latitude                                 0
Longitude                                0
Building Rentable Square Feet            0
Available Square Feet                    0
Congressional District                   0
Congressional District Representative    0
Lease Number                             0
Lease Effective Date                     0
Lease Expiration Date                    0
Real Property Asset type                 0
dtype: int64

In [18]:
# 2. Handling Numerical columns 
numeric_cols = df_copy.select_dtypes(include=['float64', 'int64']).columns
print(numeric_cols)

Index(['GSA Region', 'Zip Code', 'Latitude', 'Longitude',
       'Building Rentable Square Feet', 'Available Square Feet',
       'Congressional District'],
      dtype='object')


In [19]:
# We should keep the latitude and longitude
numeric_cols = [col for col in numeric_cols if col not in ['Latitude', 'Longitude']]

In [20]:
# Function to detect outliers using IQR method
def detect_outliers_iqr(df_copy, col):
    Q1 = df_copy[col].quantile(0.25)
    Q3 = df_copy[col].quantile(0.75)
    IQR = Q3 - Q1
    lower_bound = Q1 - 1.5 * IQR
    upper_bound = Q3 + 1.5 * IQR
    outliers = df_copy[(df_copy[col] < lower_bound) | (df_copy[col] > upper_bound)]
    return outliers

# Loop through each numerical column and check for outliers
for col in numeric_cols:
    outliers = detect_outliers_iqr(df_copy, col)
    if not outliers.empty:
        print(f"Outliers detected in {col}:")
        print(outliers[[col]])
    else:
        print(f"No outliers detected in {col}.")

No outliers detected in GSA Region.
No outliers detected in Zip Code.
Outliers detected in Building Rentable Square Feet:
      Building Rentable Square Feet
3                           89049.0
36                          75286.0
144                         76112.0
163                         96278.0
166                        587528.0
...                             ...
7507                       138168.0
7537                       284209.0
7551                        93150.0
7552                        93150.0
7553                        93150.0

[930 rows x 1 columns]
Outliers detected in Available Square Feet:
      Available Square Feet
9               3152.004900
38              2875.000000
50              1200.000000
61              9425.000000
96              6453.000000
...                     ...
7520            3599.000001
7538            1072.000000
7539            1072.000000
7540            1072.000000
7541            1072.000000

[583 rows x 1 columns]
No outliers detect

In [21]:
df_copy['Lease Effective Date'] = pd.to_datetime(df_copy['Lease Effective Date'])
df_copy['Lease Expiration Date'] = pd.to_datetime(df_copy['Lease Expiration Date'])


### Geospatial Formatting

In [22]:
import geopandas as gpd
from shapely.geometry import Point

# Create geometry points
df_copy['geometry'] = df_copy.apply(lambda row: Point(row['Longitude'], row['Latitude']), axis=1)

# Convert to GeoDataFrame
gdf = gpd.GeoDataFrame(df_copy, geometry='geometry')


In [23]:
df_copy

Location Code         Real Property Asset Name Federal Leased Code  \
0           AK0009             POST OFFICE AND CU H                   L   
1           AK3139                   TROUTTE CENTER                   L   
2           AK3166                   PETERSON TOWER                   L   
3           AK3177             TUDOR BUSINESS CNTER                   L   
4           AK3180                 MICHAEL BUILDING                   L   
...            ...                              ...                 ...   
7583        WY1354                    BLM NEWCASTLE                   L   
7584        WY1356   NORTH DISTRICT RANGER'S OFFICE                   L   
7585        WY1357       FOREST SERVICE S.O. OFFICE                   L   
7586        WY1359  DOUGLAS FOREST SERVICE BUILDING                   L   
7587        WY1362            FIRST INTERSTATE BANK                   L   

      GSA Region        Street Address       City State  Zip Code   Latitude  \
0             10                2ND ST   WRANGELL    AK     99929  56.473949   
1             10         329 HARBOR DR      SITKA    AK     99835  57.050285   
2             10              510 L ST  ANCHORAGE    AK     99501  61.217147   
3             10       1011 E TUDOR RD  ANCHORAGE    AK     99503  61.182111   
4             10        620 E 10TH AVE  ANCHORAGE    AK     99501  61.212371   
...          ...                   ...        ...   ...       ...        ...   
7583           8  1101 WASHINGTON BLVD  NEWCASTLE    WY     82701  43.849377   
7584           8   203 YELLOWSTONE AVE       CODY    WY     82414  44.516304   
7585           8   808 MEADOW LANE AVE       CODY    WY     82414  44.514855   
7586           8    2250 E RICHARDS ST    DOUGLAS    WY     82633  42.740550   
7587           8      104 S WOLCOTT ST     CASPER    WY     82601  42.849873   

       Longitude  Building Rentable Square Feet  Available Square Feet  \
0    -132.388120                           97.0                    0.0   
1    -135.333640                          951.0                    0.0   
2    -149.904320                         5283.0                    0.0   
3    -149.863110                        89049.0                    0.0   
4    -149.872310                        25515.0                    0.0   
...          ...                            ...                    ...   
7583 -104.189720                        10643.0                    0.0   
7584 -109.095450                         6066.0                    0.0   
7585 -109.069848                        13409.0                    0.0   
7586 -105.352550                        13596.0                    0.0   
7587 -106.324030                         3600.0                    0.0   

      Congressional District Congressional District Representative  \
0                        200                          MARY PELTOLA   
1                        200                          MARY PELTOLA   
2                        200                          MARY PELTOLA   
3                        200                          MARY PELTOLA   
4                        200                          MARY PELTOLA   
...                      ...                                   ...   
7583                    5600                       HARRIET HAGEMAN   
7584                    5600                       HARRIET HAGEMAN   
7585                    5600                       HARRIET HAGEMAN   
7586                    5600                       HARRIET HAGEMAN   
7587                    5600                       HARRIET HAGEMAN   

     Lease Number Lease Effective Date Lease Expiration Date  \
0        LAK00348           2022-10-01            2027-09-30   
1        LAK07113           2009-04-17            2029-04-16   
2        LAK07230           2011-05-12            2028-12-31   
3        LAK07436           2015-11-22            2035-11-21   
4        LAK06502           2003-05-01            2028-04-30   
...           ...            

In [24]:
df = df_copy.copy()

## Normalize the Data 

In [ ]:
# Create a DataFrame with the numerical features and their skewness
skew_df = pd.DataFrame(numeric_cols, columns=['Feature'])

# Calculate skewness for each numerical feature
skew_df['Skew'] = skew_df['Feature'].apply(lambda feature: scipy.stats.skew(df_copy[feature].dropna()))

# Calculate the absolute skewness
skew_df['Absolute Skew'] = skew_df['Skew'].apply(abs)

# Flag features that are skewed based on a threshold (e.g., skewness >= 0.6)
skew_df['Skewed'] = skew_df['Absolute Skew'].apply(lambda x: True if x >= 0.6 else False)

# Display the resulting DataFrame
print(skew_df)


                         Feature       Skew  Absolute Skew  Skewed
0                     GSA Region   0.143555       0.143555   False
1                       Zip Code   0.046035       0.046035   False
2  Building Rentable Square Feet   7.337146       7.337146    True
3          Available Square Feet  22.182678      22.182678    True
4         Congressional District   0.148223       0.148223   False


In [ ]:
from sklearn.preprocessing import MinMaxScaler

if (df_copy['Building Rentable Square Feet'] <= 0).any() or (df_copy['Available Square Feet'] <= 0).any():
    # Shift the values to make them positive for log transformation
    df_copy['Building Rentable Square Feet'] = df_copy['Building Rentable Square Feet'] - df_copy['Building Rentable Square Feet'].min() + 1
    df_copy['Available Square Feet'] = df_copy['Available Square Feet'] - df_copy['Available Square Feet'].min() + 1

# Apply log transformation to reduce skewness
df_copy['BRSQ_normalized'] = np.log(df_copy['Building Rentable Square Feet'])
df_copy['ASQ_normalized'] = np.log(df_copy['Available Square Feet'])

# Scale the normalized data to bring values between 0 and 1
scaler = MinMaxScaler()
df_copy[['BRSQ_normalized', 'ASQ_normalized']] = scaler.fit_transform(df_copy[['BRSQ_normalized', 'ASQ_normalized']])

## Encode Categorical Variable

In [ ]:
categorical_col = df_copy.select_dtypes(include=['object', 'category']).columns
categorical_col

Index(['Location Code', 'Real Property Asset Name', 'Federal Leased Code',
       'Street Address', 'City', 'State',
       'Congressional District Representative', 'Lease Number',
       'Real Property Asset type', 'geometry'],
      dtype='object')

In [ ]:
for column in categorical_col:
    num_unique = df_copy[column].nunique()
    unique_values = df_copy[column].unique()
    print(f"Unique values in column '{column}': {num_unique}")
    print(unique_values)
    print()

Unique values in column 'Location Code': 6485
['AK0009' 'AK3139' 'AK3166' ... 'WY1357' 'WY1359' 'WY1362']

Unique values in column 'Real Property Asset Name': 6532
['POST OFFICE AND CU H' 'TROUTTE CENTER' 'PETERSON TOWER' ...
 'FOREST SERVICE S.O. OFFICE' 'DOUGLAS FOREST SERVICE BUILDING'
 'FIRST INTERSTATE BANK']

Unique values in column 'Federal Leased Code': 1
['L']

Unique values in column 'Street Address': 6419
['2ND ST' '329 HARBOR DR' '510 L ST' ... '808 MEADOW LANE AVE'
 '2250 E RICHARDS ST' '104 S WOLCOTT ST']

Unique values in column 'City': 1829
['WRANGELL' 'SITKA' 'ANCHORAGE' ... 'LARAMIE' 'KEMMERER' 'NEWCASTLE']

Unique values in column 'State': 56
['AK' 'AL' 'AR' 'AS' 'AZ' 'CA' 'CO' 'CT' 'DC' 'DE' 'FL' 'GA' 'GU' 'HI'
 'IA' 'ID' 'IL' 'IN' 'KS' 'KY' 'LA' 'MA' 'MD' 'ME' 'MI' 'MN' 'MO' 'MP'
 'MS' 'MT' 'NC' 'ND' 'NE' 'NH' 'NJ' 'NM' 'NV' 'NY' 'OH' 'OK' 'OR' 'PA'
 'PR' 'RI' 'SC' 'SD' 'TN' 'TX' 'UT' 'VA' 'VI' 'VT' 'WA' 'WI' 'WV' 'WY']

Unique values in column 'Congressional Distr

In [ ]:
# Frequency Encoding for high-cardinality columns
high_cardinality_cols = ['Location Code', 'Real Property Asset Name', 'Street Address', 'City', 'Congressional District Representative', 'Lease Number']
for col in high_cardinality_cols:
    freq_map = df_copy[col].value_counts(normalize=True)
    df_copy[col + '_encoded'] = df_copy[col].map(freq_map)

# One-Hot Encoding for low-cardinality, non-ordinal columns
one_hot_cols = ['State', 'Real Property Asset type']
df_copy = pd.get_dummies(df_copy, columns=one_hot_cols, drop_first=True)

categorical_cols = high_cardinality_cols + one_hot_cols
existing_cols = [col for col in categorical_cols if col in df_copy.columns]
df_copy = df_copy.drop(columns=existing_cols)

In [ ]:
# Ensure date columns are in proper datetime format
df_copy['Lease Effective Date'] = pd.to_datetime(df_copy['Lease Effective Date'], errors='coerce')
df_copy['Lease Expiration Date'] = pd.to_datetime(df_copy['Lease Expiration Date'], errors='coerce')

# Extract Year, Month, Day, and Day of Week
df_copy['Effective Year'] = df_copy['Lease Effective Date'].dt.year
df_copy['Effective Month'] = df_copy['Lease Effective Date'].dt.month
df_copy['Effective Day'] = df_copy['Lease Effective Date'].dt.day

df_copy['Expiration Year'] = df_copy['Lease Expiration Date'].dt.year
df_copy['Expiration Month'] = df_copy['Lease Expiration Date'].dt.month
df_copy['Expiration Day'] = df_copy['Lease Expiration Date'].dt.day

# Calculate the delay in reporting (in days)
df_copy['Leasing Duration'] = (df_copy['Lease Expiration Date'] - df_copy['Lease Effective Date']).dt.days

In [ ]:
# Display the cleaned and transformed DataFrame
df_copy.head()

Federal Leased Code  GSA Region  Zip Code   Latitude  Longitude  \
0                   L          10     99929  56.473949 -132.38812   
1                   L          10     99835  57.050285 -135.33364   
2                   L          10     99501  61.217147 -149.90432   
3                   L          10     99503  61.182111 -149.86311   
4                   L          10     99501  61.212371 -149.87231   

   Building Rentable Square Feet  Available Square Feet  \
0                           98.0                    1.0   
1                          952.0                    1.0   
2                         5284.0                    1.0   
3                        89050.0                    1.0   
4                        25516.0                    1.0   

   Congressional District Lease Effective Date Lease Expiration Date  \
0                     200           2022-10-01            2027-09-30   
1                     200           2009-04-17            2029-04-16   
2                     200           2011-05-12            2028-12-31   
3                     200           2015-11-22            2035-11-21   
4                     200           2003-05-01            2028-04-30   

                        geometry  BRSQ_normalized  ASQ_normalized  \
0   POINT (-132.38812 56.473949)         0.320625             0.0   
1  POINT (-135.33364 57.0502849)         0.479617             0.0   
2  POINT (-149.90432 61.2171472)         0.599467             0.0   
3  POINT (-149.86311 61.1821109)         0.796985             0.0   
4   POINT (-149.87231 61.212371)         0.709580             0.0   

   Location Code_encoded  Real Property Asset Name_encoded  \
0               0.000132                          0.000132   
1               0.000132                          0.000132   
2               0.000132                          0.000132   
3               0.000132                          0.000132   
4               0.000132                          0.000132   

   Street Address_encoded  City_encoded  \
0                0.000132      0.000395   
1                0.000132      0.000791   
2                0.000132      0.004613   
3                0.000132      0.004613   
4                0.000132      0.004613   

   Congressional District Representative_encoded  Lease Number_encoded  \
0                                       0.011729              0.000132   
1                                       0.011729              0.000132   
2                                       0.011729              0.000132   
3                                       0.011729              0.000132   
4                                       0.011729              0.000132   

   State_AL  State_AR  State_AS  State_AZ  State_CA  State_CO  State_CT  \
0     False     False     False     False     False     False     False   
1     False     False     False     False     False     False     False   
2     False     False     False     False     False     False     False   
3     False     False     False     False     False     False     False   
4     False     False     False     False     False     False     False   

   State_DC  State_DE  State_FL  State_GA  State_GU  State_HI  State_IA  \
0     False     False     False     False     False     False     False   
1     False     False     False     False     False     False     False   
2     False     False     False     False     False     False     False   
3     False     False     False     False     False     False     False   
4     False     False     False     False     False     False     False   

   State_ID  State_IL  State_IN  State_KS  State_KY  State_LA  State_MA  \
0     False     False     False     False     False     False     False   
1     False     False     False     False     False     False     False   
2     False     False     False     False     False     False     False   
3     False     False     False     False     False     False     False   
4     False     False     Fals

# Step-4: Geospatial Data Analysis and Interactive Visualization

In [25]:
import pandas as pd
import geopandas as gpd
import plotly.express as px
import plotly.graph_objects as go
from shapely.geometry import Point


### Basic Interactive Map

In [26]:
fig = px.scatter_mapbox(
    df, 
    lat="Latitude", 
    lon="Longitude", 
    hover_name="Real Property Asset Name",
    hover_data={
        "City": True, 
        "State": True, 
        "Building Rentable Square Feet": True,
        "Available Square Feet": True,
        "Lease Expiration Date": True
    },
    color="State",
    zoom=2,
    height=600
)

fig.update_layout(mapbox_style="carto-positron", title="Interactive Map of GSA-Owned and Leased Properties")
fig.show()

fig.write_html("GSA_Properties_Interactive_Map.html")

In [27]:
# Heatmap for property locations
fig = px.density_mapbox(
    df,
    lat="Latitude",
    lon="Longitude",
    z="Building Rentable Square Feet",
    radius=10,
    center={"lat": 37.5, "lon": -95},  # Center on the USA
    zoom=2.5,
    mapbox_style="open-street-map",
    title="Heatmap of Property Locations by Rentable Square Feet",
)

fig.update_layout(height=600, width=1000)
fig.show()

fig.write_html("Heatmap_for_property_locations.html")

### Choropleth Map of State-Wise Property Count

In [28]:
state_counts = df.groupby("State").size().reset_index(name="Property Count")

fig = px.choropleth(
    state_counts, 
    locations="State", 
    locationmode="USA-states",
    color="Property Count",
    color_continuous_scale="Viridis",
    scope="north america",
    title="Number of Properties by State"
)

fig.update_layout(title="State-Wise Distribution of Properties")
fig.show()

fig.write_html("state_wise_distribution_of_properties.html")


### Properties in California

In [29]:
import plotly.express as px

# Filter the dataset for California
state_ca = df[df["State"] == "CA"]

# Group by city to get the property count
ca_counts = state_ca.groupby("City").size().reset_index(name="Property Count")

# Create a bar chart for city-wise property distribution
fig = px.bar(
    ca_counts,
    x="City",
    y="Property Count",
    title="City-Wise Distribution of Properties in California",
    color="Property Count",
    color_continuous_scale="Viridis",
    labels={"Property Count": "Number of Properties", "City": "City"},
    height=600,
    width=1800
)

# Update layout for better visualization
fig.update_layout(
    xaxis={"categoryorder": "total descending"},  # Sort by property count
    title_x=0.5,  # Center the title
)

fig.show()

fig.write_html("city_wise_distribution_ca.html")


In [30]:
# Refine zoom level based on California's bounding box
fig = px.scatter_mapbox(
    state_ca,
    lat="Latitude",
    lon="Longitude",
    hover_name="Real Property Asset Name",
    hover_data={
        "City": True,
        "Building Rentable Square Feet": True,
        "Available Square Feet": True,
        "Lease Expiration Date": True,
    },
    color="City",
    size="Building Rentable Square Feet",
    zoom=5,  # Adjusted zoom level for California
    center={"lat": 37.5, "lon": -119},  # Centering map on California
    title="Federal Properties in California",
    height=600,  # Increase map height for better visibility
    width=1000,  # Increase width for a larger display
)

# Enhance map design
fig.update_layout(
    mapbox_style="open-street-map",  # Use an updated map style for clarity
    margin={"r": 10, "t": 50, "l": 10, "b": 10},  # Reduce map margins for a cleaner look
    coloraxis_colorbar={
        "title": "City",
        "tickvals": None,  # Optional: customize ticks if needed
    },
)

# Add better titles and formatting
fig.update_layout(
    title={
        "text": "Federal Properties in California (Interactive Map)",
        "y": 0.95,  # Position the title higher
        "x": 0.5,
        "xanchor": "center",
        "yanchor": "top",
    },
    font=dict(family="Arial, sans-serif", size=14),  # Use clean fonts
)

fig.show()

fig.write_html("federal_properties_ca_map.html")


#### San Diego Property Analysis

In [31]:
# Filter data for California (CA) and city San Diego
state_ca = df[df["State"] == "CA"]
san_diego = state_ca[state_ca["City"].str.upper() == "SAN DIEGO"]

# Group by city and calculate property count for California
ca_city_counts = state_ca.groupby("City").size().reset_index(name="Property Count")

# Create a map for San Diego
fig_sd = px.scatter_mapbox(
    san_diego,
    lat="Latitude",
    lon="Longitude",
    hover_name="Real Property Asset Name",
    hover_data=["Building Rentable Square Feet"],
    title="Properties in San Diego, CA",
    color_discrete_sequence=["blue"],
    mapbox_style="carto-positron",
    zoom=9
)

fig_sd.show()

fig_sd.write_html("properties_in_san_diego.html")


### Analysis of Rentable vs. Available Space

In [32]:
df['Utilization Rate (%)'] = 100 * (df['Building Rentable Square Feet'] - df['Available Square Feet']) / df['Building Rentable Square Feet']

fig = px.scatter(
    df,
    x="Building Rentable Square Feet",
    y="Available Square Feet",
    size="Building Rentable Square Feet",
    color="Utilization Rate (%)",
    hover_name="Real Property Asset Name",
    title="Rentable vs. Available Space (Bubble Size Represents Rentable Space)",
    labels={"Rentable Square Feet": "Rentable Space", "Available Square Feet": "Available Space"}
)

fig.show()

fig.write_html("rentable_vs_available_space.html")


### Lease Start and Expiration Analysis


In [33]:
# Convert lease dates to datetime
df["Lease Effective Date"] = pd.to_datetime(df["Lease Effective Date"], errors='coerce')


# Extract year from lease dates
df["Lease Start Year"] = df["Lease Effective Date"].dt.year

# Count leases by start year
lease_start_counts = df["Lease Start Year"].value_counts().reset_index()
lease_start_counts.columns = ["Year", "Lease Count"]

# Line chart for lease start trends
fig = px.line(
    lease_start_counts.sort_values("Year"),
    x="Year",
    y="Lease Count",
    title="Lease Start Trends Over Time"
)

fig.update_layout(
    xaxis_title="Year",
    yaxis_title="Number of Leases",
    title_x=0.5
)
fig.show()


fig.write_html("lease_start_trends.html")


In [34]:
df['Lease Expiration Year'] = pd.to_datetime(df['Lease Expiration Date']).dt.year

lease_counts = df.groupby("Lease Expiration Year").size().reset_index(name="Count")

fig = px.bar(
    lease_counts,
    x="Lease Expiration Year",
    y="Count",
    title="Lease Expirations by Year",
    labels={"Count": "Number of Leases"},
    text_auto=True
)

fig.show()

fig.write_html("lease_expirations_by_year.html")

In [35]:


# Group by year of lease expiration
lease_expiration = df["Lease Expiration Date"].dt.year.value_counts().reset_index()
lease_expiration.columns = ["Year", "Count"]
lease_expiration = lease_expiration.sort_values("Year")

# Line chart for lease expiration timeline
fig = px.line(
    lease_expiration,
    x="Year",
    y="Count",
    title="National Lease Expiration Timeline",
    markers=True,
    labels={"Year": "Year", "Count": "Number of Leases Expiring"},
    height=600,
    width=1000,
)

fig.update_layout(
    xaxis_title="Year",
    yaxis_title="Number of Expiring Leases",
    title_x=0.5,
)

fig.show()

fig.write_html("lease_expiration_timeline.html")


#### Top 10 States with the Most Properties

In [36]:
# Top states by property count
top_states = state_counts.sort_values("Property Count", ascending=False).head(10)

# Bar chart for top states
fig = px.bar(
    top_states,
    x="State",
    y="Property Count",
    title="Top 10 States with the Most Properties",
    color="Property Count",
    color_continuous_scale="Viridis",
    text="Property Count",
    height=600,
    width=1000,
)

fig.update_layout(
    xaxis_title="State",
    yaxis_title="Number of Properties",
    title_x=0.5,
)

fig.show()

fig.write_html("top_10_states_with_most_properties.html")


#### Congressional District Representative Analysis

In [37]:
df["Congressional District Representative"].value_counts()

Congressional District Representative
ELEANOR NORTON              167
JENNIFFER GONZALEZ-COLON     96
MARY PELTOLA                 89
DONALD BEYER                 86
GERALD CONNOLLY              75
                           ... 
GARY PALMER                   2
YVETTE CLARKE                 1
BRIAN FITZPATRICK             1
MICHAEL BURGESS               1
DANIEL WEBSTER                1
Name: count, Length: 438, dtype: int64

In [38]:
# Group properties by Representative
representative_counts = df.groupby("Congressional District Representative").size().reset_index(name="Property Count")

# Bar chart for top 10 Representatives with most properties in their district
fig = px.bar(
    representative_counts.sort_values("Property Count", ascending=False).head(10),
    x="Congressional District Representative",
    y="Property Count",
    color="Property Count",
    color_continuous_scale="Plasma",
    title="Top 10 Representatives with Most Properties in Their Districts",
    text="Property Count"
)

fig.update_layout(
    xaxis_title="Congressional District Representative",
    yaxis_title="Number of Properties",
    title_x=0.5,
    height=600,
    width=1200
)
fig.show()

fig.write_html("top_10_representatives_with_most_properties.html")


#### Asset Type Analysis

In [39]:
df["Real Property Asset type"].value_counts()

Real Property Asset type
BUILDING     7449
STRUCTURE     122
LAND           17
Name: count, dtype: int64

In [40]:
# Group data by Asset Type
asset_type_counts = df.groupby("Real Property Asset type").size().reset_index(name="Property Count")

# Bar chart for Asset Type distribution
fig = px.bar(
    asset_type_counts.sort_values("Property Count", ascending=False),
    x="Real Property Asset type",
    y="Property Count",
    color="Property Count",
    color_continuous_scale="Blues",
    title="Distribution of Real Property Asset Types",
    text="Property Count"
)

fig.update_layout(
    xaxis_title="Real Property Asset Type",
    yaxis_title="Number of Properties",
    title_x=0.5,
    height=600,
    width=900
)
fig.show()

fig.write_html("distribution_of_real_property_asset_types.html")


In [41]:
# Group by State and Real Property Asset Type
state_asset_counts = df.groupby(["State", "Real Property Asset type"]).size().reset_index(name="Property Count")

# Choropleth with Asset Type breakdown
fig = px.choropleth(
    state_asset_counts,
    locations="State",
    locationmode="USA-states",
    color="Property Count",
    facet_col="Real Property Asset type",
    color_continuous_scale="Viridis",
    title="Distribution of Property Types by State"
)

fig.update_layout(height=700, width=1200)
fig.show()

fig.write_html("property_types_by_state.html")

## Advanced Analysis

### Proximity Analysis on properties within a 10 km radius from center of San Diego City


In [94]:
from geopy.distance import geodesic


san_diego_center = (32.7157, -117.1611)

# Calculating distances
df["Distance from San Diego"] = df[["Latitude", "Longitude"]].apply(
    lambda x: geodesic(san_diego_center, (x["Latitude"], x["Longitude"])).km, axis=1
)

# Filtering properties within 10 km
nearby_properties = df[df["Distance from San Diego"] <= 10]

# Visualizing these properties on a map
fig = px.scatter_mapbox(
    nearby_properties,
    lat="Latitude",
    lon="Longitude",
    hover_name="Real Property Asset Name",
    title="Properties within 10km of San Diego Center",
    mapbox_style="open-street-map"
)
fig.show()


### Spatial Clustering of Properties

In [ ]:
fig = px.scatter_mapbox(
    df,
    lat="Latitude",          # Latitude column
    lon="Longitude",         # Longitude column
    color="Cluster",        
    size=None,              
    hover_name="Real Property Asset Name",  
    hover_data={"City": True, "State": True, "Cluster": True},  
    title="Property Clusters by DBSCAN",
    color_discrete_sequence=px.colors.qualitative.Set1, 
    height=600,
    opacity=0.7
)

# Configuring Mapbox settings
fig.update_layout(
    mapbox=dict(
        style="carto-positron",  
        zoom=2,                 # Adjust zoom level
        center=dict(lat=df["Latitude"].mean(), lon=df["Longitude"].mean()),  # Center map
    ),
    margin={"r":0, "t":40, "l":0, "b":0},  
)

fig.show()


### Integrating Population Dataset for Properties and Population Estimates

In [160]:


# Loading the population dataset
population_data = pd.read_csv("population_USA.csv", encoding='latin1')

# Cleaning the 'Geographic Area' in the population dataset to extract just the city name
population_data['City'] = population_data['Geographic Area'].str.split(',').str[0].str.strip()
population_data['City'] = population_data['City'].str.replace(' city', '', regex=False).str.upper()

# Counting the number of properties per city
property_count = df.groupby('City').size().reset_index(name='Property Count')

# Merging the two datasets on the 'City' column to get population and property count
merged_df = pd.merge(df, population_data[['City', 'Population 2023']], 
                     left_on="City", right_on="City", how="inner")
merged_df = pd.merge(merged_df, property_count, on="City", how="left")

# Creating an interactive map without Mapbox using scatter_geo
fig = px.scatter_geo(
    merged_df,
    lat="Latitude",           
    lon="Longitude",         
    color="City",              
    hover_name="City",        
    hover_data=["Population 2023", "Property Count"],  
    title="Properties and Population Estimates"
)

fig.update_layout(
    mapbox_zoom=2,  # Initial zoom level 
    mapbox_center={"lat": merged_df["Latitude"].mean(), "lon": merged_df["Longitude"].mean()},
    showlegend=True,
    title="Properties and Population Estimates",
    geo=dict(showcoastlines=True, coastlinecolor="Black", projection_scale=5)
)

fig.show()
